# Sub-annual velocity time series

In [1]:
# EXPECTED RUNTIME: 40 sec

import geopandas as gpd
import numpy as np
import xarray as xr

# Metadata for output Dataset
ATTRS = {
    "cd": {
        "description": "Distance of point along centre flowline of glacier",
        "units": "metres from minimum observed terminus position (positive=upstream)",
    },
    "glacier_code": {
        "description": "Initials of glacier",
    },
    "v": {
        "description": "median velocity magnitude sampled within a 1x1 km box about point (x,y)",
        "units": "metre/year",
    },
    "v_error": {
        "description": "median velocity magnitude error sampled within a 1x1 km box about point (x,y)",
        "units": "metre/year",
    },
    "x": {
        "description": "x coordinate of projection",
        "units": "metres",
    },
    "y": {
        "description": "y coordinate of projection",
        "units": "metres",
    },
}

# Variables to extract from datacubes
VARIABLES = [
    "v",
    "v_error",
    "date_dt",
    "mid_date",
    "mission_img1",
    "satellite_img1",
    "acquisition_date_img1",
    "acquisition_date_img2",
    "mapping",
]

# Read, sort, and subset centreline points
points = gpd.read_file("../data/misc/centreline_points.geojson")
points = points.sort_values(by=["glacier_code", "cd"])
points = points.loc[points.cd.isin([1_000, 10_000])].reset_index()

# Read ITS_LIVE datacube catalog and reproject to EPSG:3413
its_live_catalog_url = "https://its-live-data.s3-us-west-2.amazonaws.com/datacubes/catalog_v02.json"
its_live_catalog = gpd.read_file(its_live_catalog_url).to_crs(3413)

# Overlay points with datacube catalog to get intersecting datacube URLs (and modify to s3 format)
points = points.overlay(its_live_catalog[["geometry", "zarr_url"]], how="intersection")
points["zarr_url"] = points.zarr_url.str.replace("http:", "s3:")
points["zarr_url"] = points.zarr_url.str.replace(".s3.amazonaws.com", "")

# To store sampled Datasets
v_ds = []

# Group centreline points by intersecting datacube
for zarr_url, points_cube in points.groupby(by="zarr_url"):
    # Open datacube
    its_live = xr.open_dataset(zarr_url, engine="zarr", storage_options={"anon": True})

    # Group points by glacier
    for _, points_glacier in points_cube.groupby(by="glacier_code"):
        # Iterate over each point for current glacier
        for i, point in points_glacier.reset_index().iterrows():
            # Define slices for x and y bounds of 1km sampling box about point
            x = point.geometry.x
            y = point.geometry.y
            x_slice = slice(x - 500, x + 500)
            y_slice = slice(y + 500, y - 500)

            # Subset ITS_LIVE dataset by sampling box, selecting only variables of
            _v_ds = its_live[VARIABLES].sel(x=x_slice, y=y_slice)

            # Lazily sample median v and v_error
            _v_ds["v"] = _v_ds.v.median(dim=["x", "y"]).assign_attrs(ATTRS["v"])
            _v_ds["v_error"] = _v_ds.v_error.median(dim=["x", "y"]).assign_attrs(ATTRS["v_error"])

            # Assign dimensions of current point as (glacier_code, cd)
            _v_ds = _v_ds.drop_dims(drop_dims=["x", "y"])
            _v_ds = _v_ds.expand_dims(dim=["glacier_code", "cd"])
            _v_ds = _v_ds.assign_coords(
                cd=("cd", [point.cd], ATTRS["cd"]),
                glacier_code=("glacier_code", [point.glacier_code], ATTRS["glacier_code"]),
                x=(("glacier_code", "cd"), [[point.geometry.x]], ATTRS["x"]),
                y=(("glacier_code", "cd"), [[point.geometry.y]], ATTRS["y"]),
            )
            v_ds.append(_v_ds)

# Concat sampled Datasets and write to disk
v_ds = xr.combine_nested(v_ds, concat_dim="mid_date", combine_attrs="drop_conflicts")
v_ds.to_netcdf("../data/velocity/velocity_points_sub-annual_1985_2022.nc")
v_ds

<xarray.Dataset> Size: 81MB
Dimensions:                (glacier_code: 2, cd: 2, mid_date: 348436)
Coordinates:
  * cd                     (cd) int32 8B 1000 10000
  * glacier_code           (glacier_code) <U2 16B 'DJ' 'UI'
  * mid_date               (mid_date) datetime64[ns] 3MB 2019-07-12T14:00:21....
    x                      (glacier_code, cd) float64 32B 5.571e+05 ... 4.809...
    y                      (glacier_code, cd) float64 32B -1.896e+06 ... -2.4...
Data variables:
    v                      (glacier_code, cd, mid_date) float32 6MB nan ... nan
    v_error                (glacier_code, cd, mid_date) float32 6MB nan ... nan
    date_dt                (glacier_code, cd, mid_date) timedelta64[ns] 11MB ...
    mission_img1           (glacier_code, cd, mid_date) object 11MB nan ... nan
    satellite_img1         (glacier_code, cd, mid_date) object 11MB nan ... nan
    acquisition_date_img1  (glacier_code, cd, mid_date) datetime64[ns] 11MB N...
    acquisition_date_img2  (glacier_code, cd, mid_date) datetime64[ns] 11MB N...
    mapping                (mid_date, glacier_code, cd) object 11MB nan ... nan
Attributes:
    Conventions:                CF-1.8
    GDAL_AREA_OR_POINT:         Area
    author:                     ITS_LIVE, a NASA MEaSUREs project (its-live.j...
    autoRIFT_parameter_file:    http://its-live-data.s3.amazonaws.com/autorif...
    datacube_software_version:  1.0
    institution:                NASA Jet Propulsion Laboratory (JPL), Califor...
    projection:                 3413
    time_standard_img1:         UTC
    time_standard_img2:         UTC
    title:                      ITS_LIVE datacube of image pair velocities

In [2]:
# EXPECTED RUNTIME: 15 sec

import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.dates import DateFormatter, YearLocator
from matplotlib.gridspec import GridSpec
from matplotlib.offsetbox import AnchoredText

SETTINGS = {
    "DJ": {
        "colour": [(0.122, 0.467, 0.706, 1.0), (0.122, 0.467, 0.706, 0.25)],
        "label": "Daugaard-Jensen",
    },
    "UI": {
        "colour": [(1.0, 0.498, 0.055, 1.0), (1.0, 0.498, 0.055, 0.25)],
        "label": "Uunartit Islands",
    },
}

# Global plot settings
plt.rcParams["figure.dpi"] = 1000
plt.rcParams["font.family"] = "Times New Roman"
plt.rcParams["font.size"] = 18
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["xtick.labelsize"] = 18
plt.rcParams["ytick.labelsize"] = 18

# Set up axes
fig = plt.figure(figsize=(16, 6))
gs = GridSpec(nrows=1, ncols=2, width_ratios=[1, 2], height_ratios=[1])
ax0 = fig.add_subplot(gs[0, 0])
ax1 = fig.add_subplot(gs[0, 1:])
axs = [ax0, ax1]

# Define temporal slices for each axis
time_slices = [slice("1985-01-01", "2010-01-01"), slice("2010-01-01", "2024-01-01")]

# Select point 1 km upstream from terminus
v_ds = xr.open_dataset("../data/velocity/velocity_points_sub-annual_1985_2022.nc")
v_ds_point = v_ds.sel(cd=1_000)

# Convert date_dt to days and use as filter to subset velocities
date_dt_days = v_ds_point.date_dt / np.timedelta64(1, "D")
v_ds_point = v_ds_point.where((date_dt_days >= 0) & (date_dt_days <= 31), drop=True)

# Resample velocities to monthly temporal resolution
v_ds_point = v_ds_point.sortby("mid_date").resample(mid_date="1MS").mean()

# Group velocity results by glacier
for glacier, v_ds_point_glacier in v_ds_point.groupby("glacier_code", squeeze=False):
    # Plot on each axis in turn
    for i, time_slice in enumerate(time_slices):
        # Select v and v_error for current time slice
        v = v_ds_point_glacier.v.sel(mid_date=time_slice).squeeze().dropna("mid_date")
        v_error = v_ds_point_glacier.v_error.sel(mid_date=time_slice).squeeze().dropna("mid_date")

        # rolling_median = (
        #     period_subset.sortby("mid_date")
        #     .v.dropna("mid_date")
        #     .rolling(mid_date=28, center=True)
        #     .median()
        # )

        # Plot data
        axs[i].errorbar(
            v.mid_date.values,
            v.values,
            v_error.values,
            label=SETTINGS[glacier]["label"],
            marker="o",
            linestyle="-",
            markersize=4,
            linewidth=2.5,
            markeredgecolor=SETTINGS[glacier]["colour"][0],
            markerfacecolor=SETTINGS[glacier]["colour"][0],
            color=SETTINGS[glacier]["colour"][1],
            ecolor=SETTINGS[glacier]["colour"][1],
            elinewidth=2,
        )
        # axs[i].plot(
        #     rolling_median.mid_date.values,
        #     rolling_median,
        #     label=SETTINGS[glacier]["label"],
        #     marker="",
        #     linestyle="-",
        #     color="black",
        #     alpha=0.5,
        #     zorder=10,
        # )


# Set y-axis range to fit data and adds label
axs[0].set_ylabel("Velocity [km a$^{-1}$]", labelpad=20)

# Set x-axis range to fit data
axs[0].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
axs[1].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))

# Set x-axis tick frequency (major)
axs[0].xaxis.set_major_locator(YearLocator(base=5))

# Disable y-axis tick labels
axs[1].tick_params(labelleft=False)

# Formatting applied to both axes
for i, ax in enumerate(axs):
    # Limit y-axis range
    ax.set_ylim(bottom=1000, top=8000)

    # Tick text format, frequency, and rotation
    ax.xaxis.set_major_formatter(DateFormatter("%Y"))
    ax.xaxis.set_minor_locator(YearLocator(1))
    ax.tick_params(axis="x", rotation=70)

    # Remove margin gap
    ax.margins(x=0)

    # Draw grid
    ax.grid(
        True,
        which="both",
        axis="both",
        c="gray",
        linestyle=":",
        linewidth=0.5,
        alpha=0.8,
        zorder=0,
    )

    # Draw axes label
    ax.add_artist(
        AnchoredText(
            f"({i})",
            loc="upper left",
            borderpad=0.1,
            prop=dict(weight="semibold"),
            frameon=False,
        )
    )

plt.tight_layout()
plt.savefig(
    "../img/velocity_sub-annual_1985_2022_time-series.png",
    dpi=fig.dpi,
    bbox_inches="tight",
)
plt.show()

# Annual velocity time series

In [111]:
# EXPECTED RUNTIME: 10 sec

import glob

import geopandas as gpd
import pandas as pd
import xarray as xr

# Metadata for output Dataset
ATTRS = {
    "cd": {
        "description": "Distance of point along centre flowline of glacier",
        "units": "metres from minimum observed terminus position (positive=upstream)",
    },
    "glacier_code": {
        "description": "Initials of glacier",
    },
    "v": {
        "description": "median velocity magnitude sampled within a 1x1 km box about point (x,y)",
        "units": "metre/year",
    },
    "v_error": {
        "description": "median velocity magnitude error sampled within a 1x1 km box about point (x,y)",
        "units": "metre/year",
    },
    "x": {
        "description": "x coordinate of projection",
        "units": "metres",
    },
    "y": {
        "description": "y coordinate of projection",
        "units": "metres",
    },
}

# Read, sort, and subset centreline points
points = gpd.read_file("../data/misc/centreline_points.geojson")
points = points.sort_values(by=["glacier_code", "cd"])
points = points.loc[points.cd.between(0, 20_000)].reset_index()

# Find file paths for all ITS_LIVE annual mosaics
files = glob.glob("../data/velocity/ITS_LIVE_velocity_120m_RGI05A_*_v02.nc")

# # OPTIONAL: Stream ITS_LIVE annual mosaics from S3 storage (avoids downloading ~35 GB)
# import s3fs
# its_live_s3 = s3fs.S3FileSystem(anon=True)
# its_live_s3_path = "s3://its-live-data/velocity_mosaic/v2/annual"
# files = its_live_s3.glob(f"{its_live_s3_path}/ITS_LIVE_velocity_120m_RGI05A_*_v02.nc")
# files = [its_live_s3.open(f, mode="rb") for f in files[1:]]

# Stack mosaics by year into lazy dask dataset
its_live = xr.open_mfdataset(files, concat_dim="time", combine="nested")

# To store point-sampled subsets of its_live
v_ds = []

# Group points by glacier
for _, points_glacier in points.groupby(by="glacier_code"):
    # Iterate over each point for current glacier
    for _, point in points_glacier.reset_index().iterrows():
        # Define slices for x and y bounds of 1km sampling box about point
        x = point.geometry.x
        y = point.geometry.y
        x_slice = slice(x - 500, x + 500)
        y_slice = slice(y + 500, y - 500)

        # Subset ITS_LIVE dataset by sampling box
        _v_ds = its_live.sel(x=x_slice, y=y_slice)

        # Sample median v and v_error (lazily)
        _v_ds["v"] = _v_ds.v.median(dim=["x", "y"]).assign_attrs(ATTRS["v"])
        _v_ds["v_error"] = _v_ds.v_error.median(dim=["x", "y"]).assign_attrs(ATTRS["v_error"])

        # Assign dimensions of current point as (glacier_code, cd), and
        # convert time dimension from index to datetime
        _v_ds = _v_ds.drop_dims(drop_dims=["x", "y"])
        _v_ds = _v_ds.expand_dims(dim=["glacier_code", "cd"])
        _v_ds = _v_ds.assign_coords(
            cd=("cd", [point.cd], ATTRS["cd"]),
            glacier_code=("glacier_code", [point.glacier_code], ATTRS["glacier_code"]),
            time=("time", [pd.to_datetime(i + 1985, format="%Y") for i in _v_ds.time.values]),
            x=(("glacier_code", "cd"), [[point.geometry.x]], ATTRS["x"]),
            y=(("glacier_code", "cd"), [[point.geometry.y]], ATTRS["y"]),
        )
        v_ds.append(_v_ds)

# Concat sampled Datasets and write to disk
v_ds = xr.combine_by_coords(v_ds, combine_attrs="drop_conflicts")
v_ds.to_netcdf("../data/velocity/velocity_points_annual_1985_2022.nc")
v_ds

<xarray.Dataset> Size: 77kB
Dimensions:       (glacier_code: 2, cd: 81, time: 38)
Coordinates:
  * cd            (cd) int32 324B 0 250 500 750 1000 ... 19250 19500 19750 20000
  * glacier_code  (glacier_code) <U2 16B 'DJ' 'UI'
  * time          (time) datetime64[ns] 304B 1985-01-01 ... 2022-01-01
    x             (glacier_code, cd) float64 1kB 5.576e+05 ... 4.74e+05
    y             (glacier_code, cd) float64 1kB -1.895e+06 ... -2.437e+06
Data variables:
    mapping       (glacier_code, cd, time) <U1 25kB '' '' '' '' ... '' '' '' ''
    v             (glacier_code, cd, time) float32 25kB dask.array<chunksize=(1, 1, 1), meta=np.ndarray>
    v_error       (glacier_code, cd, time) float32 25kB dask.array<chunksize=(1, 1, 1), meta=np.ndarray>
Attributes: (12/14)
    author:                            ITS_LIVE, a NASA MEaSUREs project (its...
    datacube_autoRIFT_parameter_file:  http://its-live-data.s3.amazonaws.com/...
    institution:                       NASA Jet Propulsion Laboratory (JPL), ...
    region:                            RGI05A
    year:                              01-Jan-1985
    GDAL_AREA_OR_POINT:                Area
    ...                                ...
    title:                             ITS_LIVE annual mosaics of image pair ...
    date_created:                      15-Mar-2024 13:00:22
    latitude:                          [71.88]
    longitude:                         [-39.83]
    s3:                                s3://its-live-data/mosaics/annual/v2_s...
    url:                               http://its-live-data.s3.amazonaws.com/...

In [123]:
# EXPECTED RUNTIME: 10 sec

import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.dates import DateFormatter, YearLocator
from matplotlib.offsetbox import AnchoredText
from matplotlib.gridspec import GridSpec

PLOT_SETTINGS = {
    "DJ": {
        "colour": [(0.122, 0.467, 0.706, 1.0), (0.122, 0.467, 0.706, 0.25)],
        "label": "Daugaard-Jensen",
    },
    "UI": {
        "colour": [(1.0, 0.498, 0.055, 1.0), (1.0, 0.498, 0.055, 0.25)],
        "label": "Uunartit Islands",
    },
}

# Global plot settings
plt.rcParams["figure.dpi"] = 1000
plt.rcParams["font.family"] = "Times New Roman"
plt.rcParams["font.size"] = 18
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["xtick.labelsize"] = 18
plt.rcParams["ytick.labelsize"] = 18

# Set up axes
fig = plt.figure(figsize=(16, 6))
gs = GridSpec(nrows=1, ncols=2, width_ratios=[1, 2], height_ratios=[1])
ax0 = fig.add_subplot(gs[0, 0])
ax1 = fig.add_subplot(gs[0, 1:])
axs = [ax0, ax1]

# Define temporal slices for each axis
time_slices = [slice("1985-01-01", "2010-01-01"), slice("2010-01-01", "2024-01-01")]

# Compute Dataset and select point 1 km upstream from terminus
v_ds = xr.open_dataset("../data/velocity/velocity_points_annual_1985_2022.nc")
v_ds_point = v_ds.sel(cd=1_000)

# Group velocity results by glacier
for glacier, v_ds_point_glacier in v_ds_point.groupby("glacier_code", squeeze=False):
    # Plot on each axis in turn
    for i, time_slice in enumerate(time_slices):
        # Select v and v_error for current time slice
        v = v_ds_point_glacier.v.sel(time=time_slice).squeeze()
        v_error = v_ds_point_glacier.v_error.sel(time=time_slice).squeeze()

        # Plot data
        axs[i].errorbar(
            v.time.values,
            v.values,
            v_error.values,
            label=PLOT_SETTINGS[glacier]["label"],
            marker="o",
            linewidth=2.5,
            color=PLOT_SETTINGS[glacier]["colour"][1],
            markersize=8,
            markeredgecolor=PLOT_SETTINGS[glacier]["colour"][0],
            markerfacecolor=PLOT_SETTINGS[glacier]["colour"][0],
            ecolor=PLOT_SETTINGS[glacier]["colour"][1],
            elinewidth=5,
            zorder=10,
            clip_on=False,
        )

# Set y-axis range to fit data and adds label
axs[0].set_ylabel("Velocity [m a$^{-1}$]", labelpad=20)

# Set x-axis range to fit data
axs[0].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
axs[1].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))

# Set x-axis tick frequency (major)
axs[0].xaxis.set_major_locator(YearLocator(base=5))

# Disable y-axis tick labels
axs[1].tick_params(labelleft=False)

# Formatting applied to both axes
for i, ax in enumerate(axs):
    # Limit y-axis range
    ax.set_ylim(bottom=2_000, top=5_500)

    # Tick text format, frequency, and rotation
    ax.xaxis.set_major_formatter(DateFormatter("%Y"))
    ax.xaxis.set_minor_locator(YearLocator(1))
    ax.tick_params(axis="x", rotation=70)

    # Remove margin gap
    ax.margins(x=0)

    # Draw grid
    ax.grid(
        True,
        which="both",
        axis="both",
        c="gray",
        linestyle=":",
        linewidth=0.5,
        alpha=0.8,
        zorder=0,
    )

    # Draw axes label
    ax.add_artist(
        AnchoredText(
            f"({i})",
            loc="upper left",
            borderpad=0.1,
            prop=dict(weight="semibold"),
            frameon=False,
        )
    )

plt.tight_layout()
plt.savefig(
    "../img/velocity_annual_1985_2022_time-series.png",
    dpi=fig.dpi,
    bbox_inches="tight",
)
plt.show()

# Misc

In [ ]:
import geopandas as gpd
import matplotlib.pyplot as plt
import xarray as xr

# Define the coordinates for the bounding box
bbox_y_min = -1866831
bbox_x_min = -312651
bbox_y_max = -1799771
bbox_x_max = -260844

centreline_lines = gpd.read_file("../data/misc/centreline_lines.geojson")
centreline_dj = centreline_lines[centreline_lines["glacier_code"] == "DJ"]

bbox_x_min, bbox_y_min, bbox_x_max, bbox_y_max = centreline_dj.total_bounds

mosaic_path = "..\\data\\velocity\\ITS_LIVE_velocity_120m_RGI05A_2022_v02.nc"

with xr.open_dataset(mosaic_path, engine="h5netcdf") as ds:
    x_slice = slice(bbox_x_min, bbox_x_max)
    y_slice = slice(bbox_y_max, bbox_y_min)

    ds_subset = ds.sel(x=x_slice, y=y_slice)
    landice_mask = ds_subset["landice"] > 0
    ds_subset = ds_subset.where(landice_mask, float("nan"))

    # Optional: Plot the subsetted data
    ds_subset["v"].plot(cmap="viridis")
    plt.plot(*centreline_dj.geometry[0].xy)
    plt.title("v")
    plt.show()

    ds_subset["v_error"].plot(cmap="viridis")
    plt.title("v_error")
    plt.show()

    ds_subset["landice"].plot(cmap="viridis")
    plt.title("landice")
    plt.show()

    ds_subset["floatingice"].plot(cmap="viridis")
    plt.title("floatingice")
    plt.show()

    ds_subset["count"].plot(cmap="viridis")
    plt.title("count")
    plt.show()